In [1]:
import os
import glob
from datetime import datetime
import pandas as pd
from plotly.graph_objs import Scatter,Layout
import plotly
import plotly.offline as py
import numpy as np
import plotly.graph_objs as go
from plotly.subplots import make_subplots
plotly.offline.init_notebook_mode(connected=True)
import gezi
import time

In [2]:
%%html
<style>
.output_wrapper, .output {
    height:auto !important;
    max-height:10000px;  /* your desired max-height here */
}
.output_scroll {
    box-shadow:none !important;
    webkit-box-shadow:none !important;
}
</style>

In [3]:
def show(dfs, names, smoothing=0., include=None, base=True,  limit=0):
  if isinstance(names, str):
    names = names.split(',')
  ori_names = names

  for name, name2 in zip(names, ori_names):
    datas = []
    for df in dfs:
        if include and include not in df.name and not df.name == 'base':
            continue
        hours=df.hour.values if not limit else df.hour.values[-limit:]
        mode = 'lines+markers' if not 'day' in df.name else 'markers'
        mode = 'lines+markers'
        if 'lines' in mode and smoothing > 0:
            mode = mode.replace('+markers', '')
        if include == 'day':
            mode = 'lines+markers'
        data = go.Scatter(
            x=[datetime.strptime(str(x), '%Y%m%d%H') for x in hours],
            y=gezi.smooth(df[name].values if not limit else df[name].values[-limit:], smoothing),
            mode=mode,
            line_shape='spline',
            line_smoothing=0.5,
            marker=dict(size=4),
            name=df.name,
        )

        datas.append(data)
   
    title = name2 if smoothing == 0 else name2 + '(smoothing%.1f)' % smoothing
    layout = go.Layout(xaxis=dict(type='date'), title=title, hovermode='x')
    fig = go.Figure(data=datas, layout=layout)
    py.iplot(fig)

In [ ]:
while True:
    root = '/home/gezi/tmp/rank/data/video_hour_sgsapp_v2/exps/monitor2/'
    root = '/home/gezi/tmp/rank/data/tuwen_hour_sgsapp_v2/exps/monitor/'
    base_dir = '/home/gezi/tmp/rank/data/tuwen_hour_sgsapp_v2/infos/15/'
    base_metric_file = os.path.join(base_dir, 'metrics_offline.csv')
    df_base = pd.read_csv(base_metric_file)
    df_base = df_base.groupby(df_base.hour, as_index=False).last()

    dfs = []
    m = {}
    start_hour = 1e32
    end_hour = -1
    for dir in glob.glob('%s/*' % root):
        if os.path.isdir(dir):
            try:
                df = pd.read_csv('%s/metric_hours.csv' % dir)
                df = df.groupby(df.hour, as_index=False).last().sort_values(by=['hour'])
                df.name = os.path.basename(dir)
                m[df.name] = df
                dfs.append(df)
                if df.hour.max() > end_hour:
                    end_hour = df.hour.max()
                if df.hour.min() < start_hour:
                    start_hour = df.hour.min()
            except Exception:
                continue

    df_base = df_base[df_base.hour > start_hour][df_base.hour < end_hour]
    if len(df_base):
        df_base.name = 'base'
        dfs.append(df_base)
        m['base'] = df_base

    for df in dfs:
        df['mean/auc'] = (df['auc'] + df['click/time_auc']) / 2
        df['group/mean/auc'] =  (df['group/auc'] + df['group/click/time_auc']) / 2
        df['wmean/auc'] = (df['auc'] + df['click/weighted_time_auc']) / 2
        df['group/wmean/auc'] =  (df['group/auc'] + df['group/click/weighted_time_auc']) / 2
        df['sqrt/auc'] = (df['auc'] * df['click/time_auc']) ** 0.5
        df['group/sqrt/auc'] =  (df['group/auc'] * df['group/click/time_auc']) ** 0.5
        df['wsqrt/auc'] = (df['auc'] * df['click/weighted_time_auc']) ** 0.5
        df['group/wsqrt/auc'] =  (df['group/auc'] * df['group/click/weighted_time_auc']) ** 0.5

    metric_names = 'gold/auc,group/auc,group/click/time_auc,auc'
    metric_names = [
        'gold/auc',
    ]
    # show(dfs, metric_names, base=False, smoothing=0.)
    dfs_ = dfs
    models = m.keys()
    dfs_ = [m[key] for key in models]
    metric_names = [
    #  'group/mean/auc',
     'group/sqrt/auc',
     'group/wsqrt/auc',
     'group/auc',
     'group/click/time_auc',
     'group/click/weighted_time_auc',
     'mean/auc',
     'wmean/auc',
     'auc',  
     'click/time_auc',
     'click/weighted_time_auc',
    ]
    models = [
    #     'base',
    # # #     'fcat.ft',
    # # #     'fcat.taskmlp.ft',
    # #     'fcat.timespan.taskmlp.ft'
    # 'timespan.taskmlp.fcat.ft.121400',
    'fcat.ft.2019122213',
        'base',
    ]
    # models += [key for key in m if key.startswith('time.') and key.endswith('hours')]
    dfs_ = [m[key] for key in set(models) if key in m]
    show(dfs_, metric_names, smoothing=0.)

In [ ]:
#metric_names = 'gold_auc,group_auc,group/click/time_auc,auc,click/time_auc,click/weighted_time_auc,time_auc,weighted_time_auc'


In [ ]:
# show(dfs_, metric_names, smoothing=0.5)

In [ ]:
# metric_names = 'gold_auc,group_auc,group/click/time_auc'
# show(dfs, metric_names, base=True, include='day')

In [ ]:
# show(dfs, 'gold_auc,group_auc,group_click_time_auc,group_click_weighted_time_auc,auc,weighted_time_auc,click_time_auc,click_weighted_time_auc', base=True)